# Proyecto 2 Ironhack. 
Analisis de Lista de Reproduccion. Generacion de una lista de reproduccion nueva

In [1]:
import base64
import requests
import datetime
from urllib.parse import urlencode
import pandas as pd

## 1. Coneccion con la API de Spotify

In [2]:
# Llaves de acceso para conectarnos a la API de Spotify
client_id = '8e5f91c2fc27453eb255a039b42bcb70'
client_secret = '09645aff5c8849f2baab977e4cfd1017'
user_id = '1279741536'

In [3]:
# Generamos esta classe que nos funcionará para que de manera automatica se genere toda la solicitud de acceso a la API

class SpotifyAPI(object):
    access_token = None
    access_token_expires = datetime.datetime.now()
    client_id = None
    client_secret = None
    access_token_did_expire = True
    token_url = 'https://accounts.spotify.com/api/token'
    
    def __init__(self, client_id, client_secret, *args, **kwargs):
        super().__init__(*args,**kwargs)
        self.client_id = client_id
        self.client_secret = client_secret
    
    # Aqui se crean las credenciales en base 64 para poder acceder a la API
    def get_client_credentials(self):
        """ returns a base64 encoded string """
        client_id = self.client_id
        client_secret = self.client_secret
        if client_secret == None or client_id == None:
            raise Exception("You must set client_id and client_secret")
            
        client_creds = f"{client_id}:{client_secret}"
        client_creds_b64 = base64.b64encode(client_creds.encode())        
        return client_creds_b64.decode()
    
    # Aqui estamos generando los headers de acceso
    def get_token_headers(self):
        client_creds_b64 = self.get_client_credentials()
        
        return {
            "Authorization":f"Basic {client_creds_b64}"
        }
    
    def get_token_data(self):
        return {
            "grant_type":"client_credentials"
        }
    
    # Aqui nos autentificamos y obtenemos el token de acceso
    def perform_auth(self):
        token_url = self.token_url
        token_data = self.get_token_data()
        token_headers = self.get_token_headers()
        
        r = requests.post(token_url, data = token_data, headers = token_headers)

        if r.status_code not in range(200,299):
            raise Exceptiontion('Could not authenticate client')
        
            
        data = r.json()
        now = datetime.datetime.now()
        acces_token = data['access_token']
        expires_in = data['expires_in'] #seconds
        expires = now + datetime.timedelta(seconds = expires_in)
        self.access_token = acces_token
        self.access_token_expires = expires
        self.access_token_did_expire = expires < now
        return True
    
    # Extraemos el token de acceso
    def get_access_token(self):
        token = self.access_token
        expires = self.access_token_expires
        now = datetime.datetime.now()
        if expires < now:
            self.perform_auth()
            return self.get_access_token()
        elif token == None:
            self.perform_auth()
            return self.get_access_token()
        return token
    
    # Aqui son los tokens de para las busquedas
    def get_resource_header(self):
        access_token = self.get_access_token()
        headers = {
            "Authorization":f"Bearer {access_token}"
        }
        return headers
        
    # busqueda de listas de reproduccion
    def get_user_playlist(self,u_id):
        endpoint = f'https://api.spotify.com/v1/users/{user_id}/playlists'
        headers = self.get_resource_header()
        r = requests.get(endpoint,headers=headers)
        if r.status_code not in range(200,299):
            return {}
        return r.json()
    
    # Busqueda de las canciones por playlist
    def get_song_playlist(self,playlist_id):
        endpoint = f'https://api.spotify.com/v1/playlists/{playlist_id}/tracks'
        headers = self.get_resource_header()
        r = requests.get(endpoint,headers=headers)
        if r.status_code not in range(200,299):
            return {}
        return r.json()
    

In [4]:
# Llamamos a la funcion y le asignamos nuestros client ID y Client Secret
spotify = SpotifyAPI(client_id,client_secret)

In [5]:
# Nos indica si fue realizada la coneccion con la API
spotify.perform_auth()

True

In [6]:
# Obtenemos el access_token que nos servirá para las consultas nescesarias. Por eso lo guardamos en una variable y que sea mas
# sencillo llamarlo posteriormente.
access_token = spotify.access_token
access_token

'BQA5bqOFGu5kdQgklDbpJW_Fg5F8LF7x6My2vrmjoT5Fu3IefMuv8n-tBFU3sdtgBLxA-W_wvHt9-x9M5nI'

In [7]:
playlist_rikrdinii = spotify.get_user_playlist(user_id)
columns = ['name','id','tracks']
pl_rikrdinii = pd.DataFrame(playlist_rikrdinii['items'],columns=columns)
pl_rikrdinii.head()


name                      id  \
0  Mis pistas en Shazam  4cneXKJlVKFLKAYuwtk57I   
1    Dubstep 2020​​   ‍  5wNRJwSnBImUuZXJW1TiAj   
2      Pure Rock & Roll  37i9dQZF1DWWRktbhJiuqL   
3          Fiesta Indie  37i9dQZF1DWSXAHZTiX76o   
4            Radio Rock  37i9dQZF1DX1te6miphixI   

                                              tracks  
0  {'href': 'https://api.spotify.com/v1/playlists...  
1  {'href': 'https://api.spotify.com/v1/playlists...  
2  {'href': 'https://api.spotify.com/v1/playlists...  
3  {'href': 'https://api.spotify.com/v1/playlists...  
4  {'href': 'https://api.spotify.com/v1/playlists...

In [24]:
id_playlist = [playlist_rikrdinii['items'][i]['id'] for i in range(len(playlist_rikrdinii['items']))]
id_playlist

['4cneXKJlVKFLKAYuwtk57I',
 '5wNRJwSnBImUuZXJW1TiAj',
 '37i9dQZF1DWWRktbhJiuqL',
 '37i9dQZF1DWSXAHZTiX76o',
 '37i9dQZF1DX1te6miphixI',
 '1Yw7Hve6LoD46LlvfGI29T',
 '37i9dQZF1DWSlJG7YPUBHF',
 '4Za3xdOwf1rgsEuEgmgJbe',
 '1Hh3HB9DCsUBI65xAq6CUG',
 '7nvh5grWo61NRk9ex0BucP',
 '6ywZrlkvzUHogLtjnZhRIx',
 '2O7wV2QZi7QYpQYsY38iqQ',
 '4XPbfflCExJlMyI2pCJDDE',
 '4r1YGed9XCLyswnoN7Tkfw',
 '7HiRRIaFkfWo3DWNFPAgJW',
 '5V0kFrendJQd01IKbO1mE8',
 '0YLFOj30e376NQoGa3oGI3',
 '1gLQQGj3Ag4AslTOBitxlF',
 '5FHSeEgQjspGl6QJeyNTho',
 '5uOZ4NdrmGuOOF2JCCdpKB']

In [ ]:
canciones = []
for id_ in id_playlist:
    canciones.append(spotify.get_song_playlist(id_))

canciones

[{'href': 'https://api.spotify.com/v1/playlists/4cneXKJlVKFLKAYuwtk57I/tracks?offset=0&limit=100',
  'items': [{'added_at': '2019-09-29T01:22:20Z',
    'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/1279741536'},
     'href': 'https://api.spotify.com/v1/users/1279741536',
     'id': '1279741536',
     'type': 'user',
     'uri': 'spotify:user:1279741536'},
    'is_local': False,
    'primary_color': None,
    'track': {'album': {'album_type': 'single',
      'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/7vk5e3vY1uw9plTHJAMwjN'},
        'href': 'https://api.spotify.com/v1/artists/7vk5e3vY1uw9plTHJAMwjN',
        'id': '7vk5e3vY1uw9plTHJAMwjN',
        'name': 'Alan Walker',
        'type': 'artist',
        'uri': 'spotify:artist:7vk5e3vY1uw9plTHJAMwjN'}],
      'available_markets': ['AD',
       'AE',
       'AL',
       'AR',
       'AT',
       'AU',
       'BA',
       'BE',
       'BG',
       'BH',
       'BO',
       'BR',
 

## 2. Busqueda y descarga de la informacion de las listas de reproduccion

In [9]:
# Documentacion para las Playlist: 
# https://developer.spotify.com/documentation/web-api/reference/playlists/get-a-list-of-current-users-playlists/

# Maximo se pueden obtener 50 listas de reproduccion
# https://api.spotify.com/v1/me/playlists" -H "Authorization: Bearer {your access token} --> Ejemplo para extraer las listas
# Tres Llamadas Get para descargar la data 

In [10]:
# Documentacion Obtencion de info de las listas de reproduccion:
# https://developer.spotify.com/documentation/web-api/reference/tracks/get-several-audio-features/

## 3. Analisis de las listas de reproduccion

## 4. Generacion de las nuevas listas de reproduccion con canciones que tengan caracteristicas similares a las de las listas de reproduccion generadas.

In [11]:
# un metodo post para subir la lista de reproduccion

## 5. BONUS: Scrapear lista de reproduccion de wikipedia de Luke Cage y generar la lista de reproduccion pertinente